# Sklearn Random Forest Regression for dp0 data

###### Load modules 

The following conditions apply:

 - env = biomass_zonal
 - data merged_slats_field_agb_dp1_start.csv

In [15]:


%matplotlib inline
import sklearn
import pandas as pd
pd.set_option('display.float_format', '{:.2f}'.format)
import numpy as np
from random import sample
from sklearn.ensemble import RandomForestRegressor as rfr
from sklearn.ensemble import ExtraTreesRegressor as etr
from sklearn.ensemble import GradientBoostingRegressor as gbr
from sklearn.ensemble import AdaBoostRegressor as abr
from sklearn.tree import DecisionTreeRegressor as dtr
import matplotlib.pyplot as plt
import csv
from sklearn.model_selection import train_test_split

# import plotting and stats modules

import matplotlib.pyplot as plt
import seaborn as sns
import os
import scipy
import scipy.stats as sc
import numpy as np
from glob import glob

# stats module
import statsmodels.api as sm
from statsmodels.tools.tools import add_constant
from statsmodels.sandbox.regression.predstd import wls_prediction_std
from statsmodels.stats.outliers_influence import variance_inflation_factor

from bokeh.io import output_notebook, output_file
from bokeh.plotting import figure, show
#%matplotlib inline

# Bokeh Libraries
# from bokeh.plotting import figure, show
# from bokeh.io import output_file
from bokeh.models import ColumnDataSource, NumeralTickFormatter, HoverTool


from sklearn.model_selection import cross_validate
#sklearn.model_selection.cross_validate
# from sklearn import cross_validation
from sklearn.metrics import explained_variance_score
from sklearn import metrics
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import GridSearchCV
#from sklearn.cross_validation import KFold
import pickle5 as Pickle

### Import data

In [16]:

csv_file = r"E:\cdu\data\compiled_data\tile_season_agb_si_zonal_stats.csv"

## Set output file locations

In [17]:
output_ = r"E:\cdu\data\ml_outputs"

In [18]:
# read as dataframe and copy
df1 = pd.read_csv(csv_file, header=0) # the first row is read in as the header for you columns
print(df1.shape) # prints out the number of rows and columns in your csv file 
print(list(df1))
df1.shape
df2 = df1.copy()

(330, 429)
['uid', 'site', 'date', 'lon_gda94', 'lat_gda94', 'bio_l_kg1ha', 'bio_t_kg1ha', 'bio_b_kg1ha', 'bio_w_kg1ha', 'bio_br_kg1ha', 'bio_s_kg1ha', 'bio_r_kg1ha', 'bio_agb_kg1ha', 'c_l_kg1ha', 'c_t_kg1ha', 'c_b_kg1ha', 'c_w_kg1ha', 'c_br_kg1ha', 'c_s_kg1ha', 'c_r_kg1ha', 'c_agb_kg1ha', 'basal_dt', 'b1_dbg_count', 'b1_dbg_min', 'b1_dbg_max', 'b1_dbg_mean', 'b1_dbg_med', 'b1_dbg_std', 'b1_dbg_p25', 'b1_dbg_p50', 'b1_dbg_p75', 'b1_dbg_p95', 'b1_dbg_p99', 'b1_dbg_range', 'b2_dbg_count', 'b2_dbg_min', 'b2_dbg_max', 'b2_dbg_mean', 'b2_dbg_med', 'b2_dbg_std', 'b2_dbg_p25', 'b2_dbg_p50', 'b2_dbg_p75', 'b2_dbg_p95', 'b2_dbg_p99', 'b2_dbg_range', 'b3_dbg_count', 'b3_dbg_min', 'b3_dbg_max', 'b3_dbg_mean', 'b3_dbg_med', 'b3_dbg_std', 'b3_dbg_p25', 'b3_dbg_p50', 'b3_dbg_p75', 'b3_dbg_p95', 'b3_dbg_p99', 'b3_dbg_range', 'b4_dbg_count', 'b4_dbg_min', 'b4_dbg_max', 'b4_dbg_mean', 'b4_dbg_med', 'b4_dbg_std', 'b4_dbg_p25', 'b4_dbg_p50', 'b4_dbg_p75', 'b4_dbg_p95', 'b4_dbg_p99', 'b4_dbg_range', 'b5_d

In [26]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

In [27]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 330 entries, 0 to 329
Columns: 429 entries, uid to MSRm
dtypes: float64(416), int64(2), object(11)
memory usage: 1.1+ MB


In [28]:
df2

uid        site      date  lon_gda94  lat_gda94  bio_l_kg1ha  \
0    125       nt001  20110523     131.21     -13.95         0.00   
1     42   barkely01  20111025     135.04     -18.00         0.00   
2     43   barkely02  20111026     135.26     -18.06         0.00   
3     45   barkely04  20111026     135.23     -17.98         0.00   
4     44   barkely03  20111026     135.29     -18.02         0.00   
5     48   barkely07  20111027     135.61     -18.09        64.00   
6     47   barkely06  20111027     135.26     -17.99         0.00   
7     46   barkely05  20111027     135.09     -17.98         0.00   
8     34  NTAGFU0001  20120412     137.07     -18.91        10.93   
9     38  NTAGFU0002  20120413     137.05     -18.92        39.34   
10    39  NTAGFU0003  20120414     137.12     -18.63       160.03   
11    40  NTAGFU0004  20120415     137.12     -18.62    437056.29   
12    41  NTAGFU0005  20120416     137.12     -18.65         6.12   
13     2       agb02  20120417     131.01     -12.65         0.00   
14    45  NTAGFU0006  20120418     136.85     -18.78    437056.29   
15    46  NTAGFU0007  20120419     136.83     -18.78    437056.29   
16    47  NTAGFU0008  20120420     136.87     -18.79    437056.29   
17    48  NTAGFU0009  20120421     136.98     -18.80         4.37   
18    52  NTAGFU0010  20120509     137.10     -17.90        43.71   
19    53  NTAGFU0011  20120510     137.07     -17.90         8.74   
20    59  NTAGFU0012  20120511     137.02     -17.90        60.71   
21    60  NTAGFU0013  20120512     137.01     -17.90        13.11   
22    68  NTAGFU0015  20120514     136.94     -17.74         4.37   
23    65  NTAGFU0014  20120514     136.94     -17.75        39.34   
24    72  NTAGFU0016  20120516     137.26     -17.22         8.74   
25    80  NTAGFU0017  20120517     137.16     -17.35    437056.29   
26    81  NTAGFU0018  20120518     137.18     -17.27    437056.29   
27    82  NTAGFU0019  20120518     137.24     -17.22        17.48   
28   112       jdr01  20120522     131.60     -13.88       458.40   
29   127       nt003  20120523     131.18     -13.85         0.00   
30   126       nt002  20120523     131.22     -13.93         0.00   
31   113       jdr02  20120523     131.60     -13.86       778.25   
32   114       jdr03  20120523     131.57     -13.85       377.78   
33   115       jdr04  20120523     131.60     -13.97       126.45   
34   128       nt004  20120524     130.86     -13.06         0.00   
35   116       jdr05  20120524     131.63     -14.11         0.00   
36    98       lim01  20120529     135.74     -16.31       177.16   
37   100       lim03  20120530     135.69     -16.45       340.87   
38   101       lim04  20120530     135.69     -16.49       107.60   
39   103       lim06  20120530     135.71     -16.31       208.28   
40    13     centa14  20120602     133.29     -14.40       271.98   
41     5     girra01  20120605     131.08     -12.51       574.77   
42    87  NTAGFU0020  20120605     135.96     -16.72        21.86   
43    92  NTAGFU0021  20120606     135.94     -16.72        57.45   
44     7      hshr01  20120606     131.06     -12.42      1265.64   
45    10      wedo01  20120606     131.01     -12.60       174.27   
46    95  NTAGFU0022  20120607     135.96     -16.73        66.11   
47    97  NTAGFU0023  20120609     135.83     -16.82    437056.29   
48    99  NTAGFU0025  20120610     135.86     -16.83        10.93   
49    98  NTAGFU0024  20120610     135.89     -16.83        23.31   
50   103  NTAGFU0026  20120612     135.41     -15.81        13.11   
51   109  NTAGFU0027  20120613     135.46     -15.68         4.37   
52   122  NTAGFU0028  20120614     135.46     -15.63         4.37   
53   130  NTAGFU0029  20120615     135.41     -15.54        13.11   
54    25       amg01  20120619     134.05     -16.38       413.63   
55    27       amg03  20120620     134.03     -16.78         0.00   
56    29       amg06  20120621     134.09     -16.69       104.28   
57 

## Fill null values in Min 02 to 0

Minimum values in FC data that has a mean value (i.e. not masked) must have a 0 minimum value

In [29]:
df2.dropna(subset = ['b1_dp0_mean'], inplace=True)

In [30]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 157 entries, 0 to 164
Columns: 429 entries, uid to MSRm
dtypes: float64(416), int64(2), object(11)
memory usage: 527.4+ KB


In [31]:
df2.b2_dp0_min.fillna(0).inplace=True

In [32]:
df2[["b2_dp0_min"]] = df2[["b2_dp0_min"]].fillna(0)

In [33]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 157 entries, 0 to 164
Columns: 429 entries, uid to MSRm
dtypes: float64(416), int64(2), object(11)
memory usage: 527.4+ KB


### Set variables to plot

In [34]:
value_x = 'b2_dp0_mean'
value_y = 'bio_agb_kg1ha'

In [35]:
df2.shape

(157, 429)

In [36]:

# Output to file
output_file(os.path.join(output_,'all_sites_{0}_{1}.html'.format(value_x, value_y)),
            title='Relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")))


#Specify the selection tools to be made available
select_tools = ['box_select', 'lasso_select', 'poly_select', 'tap', 'zoom_in', 'zoom_out', 'wheel_zoom', 'reset']

# Format the tooltip
tooltips = [
            ('Site', '@site'),
            ('Date', '@date'),
            ('AGB', '@bio_agb_kg1ha'),
#             ('Three-Point Percentage', '@pct3PM{00.0%}')   
           ]

# Create the figure
fig = figure(plot_height=400,
             plot_width=1500,
             y_axis_label= value_y.replace("_", " "), 
             x_axis_label= value_x.replace("_", " "),
             title='Relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")),
             toolbar_location='below',
             tools=select_tools)

# # Format the y-axis tick label
fig.yaxis[0].formatter = NumeralTickFormatter(format='0')

# Add square representing each site
fig.square(x= value_x,
           y= value_y,
           source=df2.round(4),
           size=5,
           color='royalblue',
           selection_color='deepskyblue',
           nonselection_color='lightgray',
           nonselection_alpha=0.3)

# Add the HoverTool to the figure
fig.add_tools(HoverTool(tooltips=tooltips))

# Visualize
show(fig)

### Drop AGB numbers which are high

In [37]:
# drop the 7 tern sites that apear to be outliers
df3 =df2[df2['bio_agb_kg1ha'] <= 100000]
df3.to_csv(os.path.join(output_, "dp1_agb_lt_100000.csv"))
drop_sites =df2[df2['bio_agb_kg1ha'] > 100000]
drop_sites.value_counts(['site', 'b2_dp0_mean', 'bio_agb_kg1ha'])


site        b2_dp0_mean  bio_agb_kg1ha
NTAMGD0004  31.25        12934706.40      1
NTAMGD0002  37.33        12934706.40      1
NTAGFU0023  42.19        12934706.40      1
NTAGFU0018  26.08        12934706.40      1
NTAGFU0017  49.81        12934706.40      1
NTAGFU0008  11.44        12934706.40      1
NTAGFU0007  16.78        12934706.40      1
NTAGFU0006  34.67        12934706.40      1
NTAGFU0004  29.75        12934706.40      1
dtype: int64

In [38]:
df3.shape

(148, 429)

In [39]:

# Output to file
output_file(os.path.join(output_, 'TERN7_removed_sites_{0}_{1}.html'.format(value_x, value_y)),
            title='Seven TERN sites removed - relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")))


#Specify the selection tools to be made available
select_tools = ['box_select', 'lasso_select', 'poly_select', 'tap', 'zoom_in', 'zoom_out', 'wheel_zoom', 'reset']

# Format the tooltip
tooltips = [
            ('Site', '@site'),
            ('Date', '@date'),
            ('AGB', '@bio_agb_kg1ha'),
#             ('Three-Point Percentage', '@pct3PM{00.0%}')   
           ]

# Create the figure
fig = figure(plot_height=400,
             plot_width=1500,
             y_axis_label= value_y.replace("_", " "), 
             x_axis_label= value_x.replace("_", " "),
             title='Seven TERN sites removed - relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")),
             toolbar_location='below',
             tools=select_tools)

# # Format the y-axis tick label
fig.yaxis[0].formatter = NumeralTickFormatter(format='0')

# Add square representing each site
fig.square(x= value_x,
           y= value_y,
           source=df3,
           size=5,
           color='royalblue',
           selection_color='deepskyblue',
           nonselection_color='lightgray',
           nonselection_alpha=0.3)

# Add the HoverTool to the figure
fig.add_tools(HoverTool(tooltips=tooltips))

# Visualize
show(fig)

### Drop the TERN sites for review

In [40]:
# drop the TERN sites due to 
df4=df3[df3.site.apply(lambda x: len(str(x))<=9)]
df4.to_csv(os.path.join(output_, "dp1_agb_NTH_only_lt_100000.csv"))

In [41]:
df4.sample(5)

uid   site      date  lon_gda94  lat_gda94  bio_l_kg1ha  bio_t_kg1ha  \
119  119  auv03  20121010     129.98     -15.71        45.58        49.57   
97    80  vrd24  20120729     131.12     -16.88         0.00         0.00   
56    29  amg06  20120621     134.09     -16.69       104.28       113.39   
32   114  jdr03  20120523     131.57     -13.85       377.78       410.80   
35   116  jdr05  20120524     131.63     -14.11         0.00         0.00   

     bio_b_kg1ha  bio_w_kg1ha  bio_br_kg1ha  bio_s_kg1ha  bio_r_kg1ha  \
119       193.67       630.06        477.79       823.73       276.96   
97          0.00         0.00          0.00         0.00         0.00   
56        443.05      1441.38       1093.02      1884.43       633.60   
32       1605.06      5221.76       3959.72      6826.82      2295.37   
35          0.00         0.00          0.00         0.00         0.00   

     bio_agb_kg1ha  c_l_kg1ha  c_t_kg1ha  c_b_kg1ha  c_w_kg1ha  c_br_kg1ha  \
119        1349.04      96.99     101.16     395.24    1285.84      975.07   
97            0.00       0.00       0.00       0.00       0.00        0.00   
56         3086.16     221.87     231.41     904.19    2941.59     2230.64   
32        11180.40     803.79     838.36    3275.64   10656.64     8081.07   
35            0.00       0.00       0.00       0.00       0.00        0.00   

     c_s_kg1ha  c_r_kg1ha  c_agb_kg1ha    basal_dt  b1_dbg_count  b1_dbg_min  \
119    1681.09     565.23      2753.14  2012-10-10          9.00      563.00   
97        0.00       0.00         0.00  2012-07-29         16.00      737.00   
56     3845.77    1293.06      6298.29  2012-06-21          9.00      129.00   
32    13932.29    4684.43     22817.14  2012-05-23          9.00      252.00   
35        0.00       0.00         0.00  2012-05-24          9.00      158.00   

     b1_dbg_max  b1_dbg_mean  b1_dbg_med  b1_dbg_std  b1_dbg_p25  b1_dbg_p50  \
119      628.00       594.33      594.00       18.63      585.00      594.00   
97       872.00       775.94      768.00       33.04      753.75      768.00   
56       247.00       171.56      160.00       31.38      153.00      160.00   
32       320.00       286.78      277.00       23.89      276.00      277.00   
35       237.00       195.00      189.00       24.68      182.00      189.00   

     b1_dbg_p75  b1_dbg_p95  b1_dbg_p99  b1_dbg_range  b2_dbg_count  \
119      597.00      624.40      627.28         65.00          9.00   
97       789.00      826.25      862.85        135.00         16.00   
56       180.00      222.20      242.04        118.00          9.00   
32       311.00      318.80      319.76         68.00          9.00   
35       196.00      236.60      236.92         79.00          9.00   

     b2_dbg_min  b2_dbg_max  b2_dbg_mean  b2_dbg_med  b2_dbg_std  b2_dbg_p25  \
119      865.00      943.00       892.22      870.00       30.43      868.00   
97      1194.00     1307.00      1249.75     1255.00       29.08     1234.00   
56       377.00      445.00       403.67      403.00       22.32      386.00   
32       451.00      538.00       505.22      492.00       30.37      483.00   
35       456.00      544.00       495.44      492.00       26.89      476.00   

     b2_dbg_p50  b2_dbg_p75  b2_dbg_p95  b2_dbg_p99  b2_dbg_range  \
119      870.00      910.00      941.80      942.76         78.00   
97      1255.00     1264.75     1286.75     1302.95        113.00   
56       403.00      416.00      439.40      443.88         68.00   
32       492.00      538.00      538.00      538.00         87.00   
35       492.00      509.00      537.20      542.64         88.00   

     b3_dbg_count  b3_dbg_min  b3_dbg_max  b3_dbg_mean  b3_dbg_med  \
119          9.00     1308.00     1396.00      1338.22     1329.00   
97          16.00     1776.00     1915.00      1846.81     1861.00   
56           9.00      474.00      604.00       516.89      508.00   
32           9.00      543.00      707.00       617.56      604.00   

In [42]:
df4.shape

(100, 429)

In [43]:

# Output to file
output_file(os.path.join(output_, 'ntg_sites_agb_{0}_{1}.html'.format(value_x, value_y)),
            title='NTG sites only - relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")))

#Specify the selection tools to be made available
select_tools = ['box_select', 'lasso_select', 'poly_select', 'tap', 'zoom_in', 'zoom_out', 'wheel_zoom', 'reset']

# Format the tooltip
tooltips = [
            ('Site', '@site'),
            ('Date', '@date'),
            ('AGB', '@bio_agb_kg1ha'),
#             ('Three-Point Percentage', '@pct3PM{00.0%}')   
           ]

# Create the figure
fig = figure(plot_height=400,
             plot_width=1500,
             y_axis_label= value_y.replace("_", " "), 
             x_axis_label= value_x.replace("_", " "),
             title='NTG sites only - relationship between {0} and {1}'.format(value_x.replace("_", " "), value_y.replace("_", " ")),
             toolbar_location='below',
             tools=select_tools)

# # Format the y-axis tick label
fig.yaxis[0].formatter = NumeralTickFormatter(format='0')

# Add square representing each site
fig.square(x= value_x,
           y= value_y,
           source=df4,
           size=5,
           color='royalblue',
           selection_color='deepskyblue',
           nonselection_color='lightgray',
           nonselection_alpha=0.3)

# Add the HoverTool to the figure
fig.add_tools(HoverTool(tooltips=tooltips))

# Visualize
show(fig)

## Choose which data set to run the models from

In [21]:
df_ml = df4

In [22]:
# drop some of the unwanted values
df_ml.drop(['uid_x', 'date', 'lon_gda94', 'lat_gda94', 'bio_l_kg1ha', 'bio_t_kg1ha', 'bio_b_kg1ha', 'bio_w_kg1ha', 'bio_br_kg1ha', 'bio_s_kg1ha', 'bio_r_kg1ha', 'c_l_kg1ha', 'c_t_kg1ha', 'c_b_kg1ha', 'c_w_kg1ha', 'c_br_kg1ha', 'c_s_kg1ha', 'c_r_kg1ha', 'c_agb_kg1ha'], axis=1, inplace=True)

C:\ProgramData\Anaconda3\envs\biomass_zonal\lib\site-packages\pandas\core\frame.py:4167: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [23]:
print(list(df_ml))

['site', 'bio_agb_kg1ha', 'basal_dt', 'uid_y', 'image', 'year', 'month', 'day', 'b1_dp0_min', 'b1_dp0_max', 'b1_dp0_mean', 'b1_dp0_count', 'b1_dp0_std', 'b1_dp0_med', 'b1_dp0_p25', 'b1_dp0_p50', 'b1_dp0_p75', 'b1_dp0_p95', 'b1_dp0_p99', 'b1_dp0_range', 'b2_dp0_min', 'b2_dp0_max', 'b2_dp0_mean', 'b2_dp0_count', 'b2_dp0_std', 'b2_dp0_med', 'b2_dp0_p25', 'b2_dp0_p50', 'b2_dp0_p75', 'b2_dp0_p95', 'b2_dp0_p99', 'b2_dp0_range', 'b3_dp0_min', 'b3_dp0_max', 'b3_dp0_mean', 'b3_dp0_count', 'b3_dp0_med', 'b3_dp0_p25', 'b3_dp0_p50', 'b3_dp0_p75', 'b3_dp0_p95', 'b3_dp0_p99', 'b3_dp0_range', 'b3_dp0_std', 'im_date', 'image_dt']


In [25]:
#dp0
df_ml.drop(['basal_dt', 'uid_y', 'image', 'year', 'month', 'day', 'im_date', 'image_dt', 'b1_dp0_count', 'b1_dp0_range', 'b2_dp0_count', ], axis=1, inplace=True)

C:\ProgramData\Anaconda3\envs\biomass_zonal\lib\site-packages\pandas\core\frame.py:4167: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [26]:
print(list(df_ml))

['site', 'bio_agb_kg1ha', 'b1_dp0_min', 'b1_dp0_max', 'b1_dp0_mean', 'b1_dp0_std', 'b1_dp0_med', 'b1_dp0_p25', 'b1_dp0_p50', 'b1_dp0_p75', 'b1_dp0_p95', 'b1_dp0_p99', 'b2_dp0_min', 'b2_dp0_max', 'b2_dp0_mean', 'b2_dp0_std', 'b2_dp0_med', 'b2_dp0_p25', 'b2_dp0_p50', 'b2_dp0_p75', 'b2_dp0_p95', 'b2_dp0_p99', 'b2_dp0_range', 'b3_dp0_min', 'b3_dp0_max', 'b3_dp0_mean', 'b3_dp0_count', 'b3_dp0_med', 'b3_dp0_p25', 'b3_dp0_p50', 'b3_dp0_p75', 'b3_dp0_p95', 'b3_dp0_p99', 'b3_dp0_range', 'b3_dp0_std']


In [29]:
df_ml.shape

(117, 35)

## Reduce level of 0 values

In [27]:
# due to the number of field sites with no basal collected data is stratified
no0_df = df_ml[df_ml['bio_agb_kg1ha']>0.0]
agb_0 = df_ml[df_ml['bio_agb_kg1ha']==0.0].sample(3)
some0_df = pd.concat([no0_df, agb_0])

## Select the dataset to run the models from

In [30]:
df = df_ml
df.shape

(117, 35)

In [31]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 117 entries, 0 to 179
Data columns (total 35 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   site           117 non-null    object 
 1   bio_agb_kg1ha  117 non-null    float64
 2   b1_dp0_min     115 non-null    float64
 3   b1_dp0_max     115 non-null    float64
 4   b1_dp0_mean    115 non-null    float64
 5   b1_dp0_std     115 non-null    float64
 6   b1_dp0_med     115 non-null    float64
 7   b1_dp0_p25     115 non-null    float64
 8   b1_dp0_p50     115 non-null    float64
 9   b1_dp0_p75     115 non-null    float64
 10  b1_dp0_p95     115 non-null    float64
 11  b1_dp0_p99     115 non-null    float64
 12  b2_dp0_min     85 non-null     float64
 13  b2_dp0_max     115 non-null    float64
 14  b2_dp0_mean    115 non-null    float64
 15  b2_dp0_std     115 non-null    float64
 16  b2_dp0_med     115 non-null    float64
 17  b2_dp0_p25     115 non-null    float64
 18  b2_dp0_p50

In [32]:
test = df[df['bio_agb_kg1ha']==0.0]

In [33]:
test.shape

(62, 35)

In [ ]:
df.dropna(inplace=True)

In [ ]:
df.info()

In [ ]:
col_list = df.columns.to_list()

In [ ]:
variable = col_list[4]
print(variable)

In [ ]:
variable

In [ ]:
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, LabelSet


bio_list = df['bio_agb_kg1ha'].tolist()
print(bio_list)
print('-'*50)
site_list = df['site'].tolist()
print(site_list)
print('-'*50)
var_list = df[variable].tolist()
print(var_list)
print('-'*50)
bio_max = max(bio_list)*1.4
print(bio_max)
print('-'*50)
var_max = max(var_list)*1.4
print(var_max)
print('-'*50)
dict_=dict(
    agb= bio_list,
    var = var_list,
    names=site_list)

print(dict_)
dict_[variable] = dict_.pop('var')
dict_
print(dict_)

print(type(variable))
source = ColumnDataSource(data=dict_)

#dictionary[new_key] = dictionary.pop(old_key)

p = figure(x_range=(var_max, bio_max))
p.scatter(x='agb', y=variable, size=8, source=source)
p.xaxis.axis_label = 'AGB'
p.yaxis.axis_label = variable

labels = LabelSet(x='agb', y=variable, text='names', level='glyph',
                  x_offset=5, y_offset=5, source=source, render_mode='canvas')


p.add_layout(labels)

show(p)

In [ ]:
for i in df.columns[1:]:
    print(i)
    value_x = 'bio_agb_kg1ha'
    value_y = str(i)
    plt.figure(figsize=(10,4))
    # left plot
    plt.subplot(1,2,1)
    sns.regplot(df[value_x], df[value_y], line_kws={"color":"red"})
    plt.xlabel(value_x)
    plt.ylabel(value_y)
    plt.title("Regression {0} and {1}".format(value_x, value_y))
    
    slope, intercept, r_value, p_value, std_err = scipy.stats.linregress(df[value_x], df[value_y])

    print("slope: ", slope)
    print("intersept: ", intercept)
    print("r2: ", r_value)
    print("P_value: ", p_value)
    print("std error: ", std_err)

    # right plot
    plt.subplot(1,2,2)
    sns.regplot(df[value_x], df[value_y], lowess=True, line_kws={"color":"green"})
    plt.xlabel(value_x)
    plt.ylabel("Error")
    plt.title("Residual Error {0} and {1}".format(value_x, value_y))
    plt.tight_layout()
    plt.show()
    
#     slope, intercept, r_value, p_value, std_err = scipy.stats.linregress(df[value_x], df[value_y])

#     print("slope: ", slope)
#     print("intersept: ", intercept)
#     print("r2: ", r_value)
#     print("P_value: ", p_value)
#     print("std error: ", std_err)

In [ ]:
value_x = 'bio_agb_kg1ha'
value_y = 'b2_dbi_mean'
sns.regplot(x= value_x, y=value_y, data=df)
slope, intercept, r_value, p_value, std_err = scipy.stats.linregress(df[value_x], df[value_y])

print("slope: ", slope)
print("intersept: ", intercept)
print("r2: ", r_value)
print("P_value: ", p_value)
print("std error: ", std_err)

In [ ]:
value_x = 'bio_agb_kg1ha'
value_y = 'b3_dbi_mean'
sns.scatterplot(x= value_x, y=value_y, data=df)
slope, intercept, r_value, p_value, std_err = scipy.stats.linregress(df[value_x], df[value_y])

print("slope: ", slope)
print("intersept: ", intercept)
print("r2: ", r_value)
print("P_value: ", p_value)
print("std error: ", std_err)

In [ ]:
# randomly split data into train and test datasets, the user needs to define the variables 

# Two example of how you can call the predictor variables 

#xdata1 = df4[df4.columns[12:]].astype('float32')

#xdata1 = df[['psB2a', 'psB3a', 'psB4a', 'psB5a', 'psB6a', 'ratio32a', 'ratio42a', 'ratio43a', 'ratio52a', 'ratio53a', 'ratio54a', 'ratio62a', 'ratio63a', 'ratio64a', 'ratio65a', 'GSAVIa', 'GNDVIa', 'CVIa', 'NDGIa', 'RIa', 'NBRa', 'NDIIa', 'GDVIa', 'MSAVIa', 'DVIa', 'SAVIa', 'NDVIa', 'MSRa', 'psB2d', 'psB3d', 'psB4d', 'psB5d', 'psB6d', 'ratio32d', 'ratio42d', 'ratio43d', 'ratio52d', 'ratio53d', 'ratio54d', 'ratio62d', 'ratio63d', 'ratio64d', 'ratio65d', 'GSAVId', 'GNDVId', 'CVId', 'NDGId', 'RId', 'NBRd', 'NDIId', 'GDVId', 'MSAVId', 'DVId', 'SAVId', 'NDVId', 'MSRd']].astype('float32')
#xdata1 = df[['psB1a', 'psB2a', 'psB3a', 'psB4a', 'psB5a', 'psB6a', 'ratio32fa', 'ratio42fa', 'ratio43fa', 'ratio52fa', 'ratio53fa', 'ratio54fa', 'ratio62fa', 'ratio63fa', 'ratio64fa', 'ratio65fa', 'ratio32a', 'ratio42a', 'ratio43a', 'ratio52a', 'ratio53a', 'ratio54a', 'ratio62a', 'ratio63a', 'ratio64a', 'ratio65a', 'GSAVIfa', 'GSAVIa', 'GNDVIfa', 'GNDVIa', 'CVIfa', 'CVIa', 'NDGIfa', 'NDGIa', 'RIfa', 'RIa', 'NBRfa', 'NBRa', 'NDIIfa', 'NDIIa', 'GDVIfa', 'GDVIa', 'MSAVIfa', 'MSAVIa', 'DVIfa', 'DVIa', 'SAVIfa', 'SAVIa', 'NDVIfa', 'NDVIa', 'MSRfa', 'MSRa']]
xdata1 = df.iloc[:, 1:].astype('float32')
ydata1 = df[['bio_agb_kg1ha']].astype('float32')
ydata2 = ydata1.values
ydata = ydata2.ravel()

X_1, X_2, y_1, y_2 = train_test_split(xdata1, ydata, train_size=0.80)  
         
print(X_1.shape, y_1.shape)
print(X_2.shape, y_2.shape)

### Plot up Histograms of Lidar meanCHM for train and test datasets

In [ ]:
plt.subplot(2, 2, 1)
plt.hist(y_1)
plt.subplot(2, 2, 2)
plt.hist(y_2)
plt.tight_layout()

### Parameterise the Random Forest Regressor alogorthim

for details see: http://scikit-learn.org/stable/modules/generated/sklearn.ensemble.RandomForestRegressor.html

In [ ]:
rng = np.random.RandomState(1)
rfrModel_1 = abr(dtr(max_depth=4), n_estimators=300, random_state=rng)
rfrModel_1

In [ ]:
rfrModel_1 = gbr(n_estimators=100, learning_rate=0.1, max_depth=1, random_state=0, loss='ls')
rfrModel_1,

In [ ]:
rfrModel_1 = etr(n_estimators=100, bootstrap=True, oob_score=True,  max_features='log2', min_samples_split=1,n_jobs=-1) 
rfrModel_1,

In [ ]:
rfrModel_1 = rfr(n_estimators=100, oob_score=True,  max_depth=None, max_features='log2', min_samples_split=1.0,n_jobs=-1) 
rfrModel_1,

In [ ]:
rfrModel_1 = rfr(n_estimators=100, oob_score=True) #,  max_depth=None, max_features='log2', min_samples_split=1.0,n_jobs=-1) 
rfrModel_1,

In [ ]:
np.nan_to_num(X_1)

### Fit random forest regressor model and compute variable importance score 

may need to restrict the number of variables for the bar graph to be legible



In [ ]:
rfrLCHM = rfrModel_1.fit(X_1, y_1)

##### good info on the feature importance score - http://stackoverflow.com/questions/15810339/how-are-feature-importances-in-randomforestclassifier-determined

In [ ]:
feature_importance = rfrModel_1.feature_importances_

### TRY THIS
# use "feature importance" scores to see what the top 10 important features are
fi = enumerate(rfrModel_1.feature_importances_)
cols = xdata1.columns
fiResult = [(value,cols[i]) for (i,value) in fi]
#fiResult = [(value,cols[i]) for (i,value) in fi if value > 0.001]
## Change the value 0.04 which we picked empirically to give us 10 variables
## try running this code after changing the value up and down so you get more or less variables
## do you see how this might be useful in refining the model?
## Here is the code in case you mess up the line above
## [(value,cols[i]) for (i,value) in fi if value > 0.04]
#print fiResult

print('Fitted model r2 =' ,  format(rfrLCHM.score(X_1, y_1), '.2f'))
print('Fitted model mse =', format(np.mean((y_1 - rfrLCHM.predict(X_1))**2), '.2f'))
print('n =', len(y_1))
plt.scatter(rfrLCHM.predict(X_1), y_1,)  
# data for the 1 for 1 line
x = [0,100]
y = [0,100]

#sets the limits of the axis
#plt.xlim(-1,35)
#plt.ylim(-1,35)

plt.ylabel('Observed AGB')

plt.xlabel('Predicted AGB')

# 1 for 1 line

plt.plot(x, y, color = 'r')
plt.show()

In [ ]:
fiResult = np.array(fiResult)
score = (fiResult[:,0])
band = fiResult[:,1]
a = fiResult[np.argsort(fiResult[:, 1])]

df = pd.DataFrame(dict(band=band,n=score))
#print(df)
df['n'].astype('float')
#df.convert_objects(convert_numeric=True).dtypes()
#ind = np.arange(len(df))
dfsort = df.sort_values(['n'], ascending=[False])
print(dfsort)
 
## my complicated way to get the bar plot to sort in ascending order and display the assocated band names in the y axis
 
dfsort2 = df.sort_values(['n'], ascending=[True])
b = dfsort2[['band']]
c = b.values.tolist()
# convert the list of band names in the correct order to a string
e = str(c)
# strips all the rubbish from the string
f = e.replace('[','').replace(']','').replace("'",'').replace(",",' ')
# convert the cleaned up string back into a list to plot the band names in the bar graph
g = f.split()
 
ind = np.arange(len(df))
width = 0.4
 
fig, ax = plt.subplots()
ax.barh(ind, dfsort2.n, width, color='blue')
ax.set(yticks=ind + width, yticklabels= g, ylim=[2*width - 1, len(df)])
plt.show()
fig.savefig('Band_Importance_Score.pdf',dpi=600)# save out your figure to a pdf 

In [ ]:
y2_predict

In [ ]:
y_2

### Predict the selected model on the test data

In [ ]:
plt.scatter(y2_predict, y_2)
plt.show()

In [ ]:
y2_predict = rfrLCHM.predict(X_2)

print('Predicted data r2 =', rfrLCHM.score(X_2, y_2))
print('MSE =', format(np.mean((y_2 - rfrLCHM.predict(X_2))** 2), '.3f'))
print('RMSE =', format(np.sqrt(np.mean((y2_predict - y_2) ** 2)), '.3f'))
#print 'explained_var =',format(explained_variance_score(y_2, y2_predict),  '.3f') 
print('bias =' , format(np.mean(y_2) - np.mean(y2_predict), '.3f'))
print('n =' , len(y_2))

plt.scatter(y2_predict, y_2 ,s=10, c='b', marker='o')
# data for the 1 for 1 line
x = [-1,30000]
y = [-1,30000]

#sets the limits of the axis
plt.xlim(-1,30000)
plt.ylim(-1, 30000)
plt.ylabel('Observed mean AGB')
plt.xlabel('Predicted mean AGB')
# 1 for 1 line
plt.plot(x, y, color = 'r')

plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde

# data to plot
x = y2_predict
y = y_2

# Calculate the point density
xy = np.vstack([x,y])
z = gaussian_kde(xy)(xy)

# Sort the points by density, so that the densest points are plotted last
idx = z.argsort()
x, y, z = x[idx], y[idx], z[idx]


fig, ax = plt.subplots()
ax.scatter(x, y, c=z, s=0.8, edgecolor='')

# data for the 1 for 1 line
a = [-1,25]
b = [-1,25]

#sets the limits of the axis
plt.xlim(-1,25)
plt.ylim(-1,25)
plt.ylabel('Observed mean CHM')
plt.xlabel('Predicted mean CHM')
# 1 for 1 line
ax.plot(a, b, color = 'black')

plt.show()

# =================================================================

# STOP - do you realy want to save this model?

# remember to change the cPickle file name !!

# Save current fitted model and apply to unseen validation data 

In [ ]:
import cPickle

#rfrL8CHM = rfr()
#rfrL8CHM.fit(X_1, y_1)

with open('rfr_modelName_nt100_n17', 'wb') as f:
    cPickle.dump(rfrLCHM, f)

In [ ]:
# read in your validation dataset which has never been seen by rfr model - NOTE in this example I am just reading the same data used to train the model

df = pd.read_csv('combined_val_data_l5_l7_l8.csv', header=0)
print df.shape 

In [ ]:
#df1 = df[(df['comp'] == 'l57')]
df1 = df[(df['chm'] >= 4)]

print (df1.shape)

In [ ]:
xdata2 = df1[['dem', 'ratio42', 'psB5', 'CVI', 'ratio43', 'psB2', 'ratio54', 'SAVI', 'ratio53', 'ratio52', 'psB3', 'GSAVI', 'ratio65', 'ratio63', 'ratio62', 'psB4', 'ratio32']].astype('float32')

ydata1 = df1[['chm']].astype('float32')

ydata2 = ydata1.values

ydata = ydata2.ravel()

print len(ydata1)

In [ ]:
with open('rfr_modelName_mKath', 'rb') as f:
        rf = cPickle.load(f)

        predicted = rf.predict(xdata2)

#print 'r2 =' ,  rf.score(predicted, y_2)
#print 'rmse =', np.sqrt(np.mean((y_2 - predicted)**2))
#print 'n =' , len(y_2)

print 'Predicted data r2 =', rf.score(xdata2, ydata)
print 'MSE =', format(np.mean((ydata - rf.predict(xdata2))** 2), '.3f')
print 'RMSE =', format(np.sqrt(np.mean((predicted - ydata) ** 2)), '.3f')
print 'explained_var =',format(explained_variance_score(ydata, predicted),  '.3f') 
print 'bias =' , format(np.mean(ydata) - np.mean(predicted), '.3f')
print 'n =' , len(ydata)


# plot up predicted and observed data 
plt.scatter(predicted, ydata,s=0.002, c='b', marker='o')

# data for the 1 for 1 line
x = [-1,30]
y = [-1,30]

#sets the limits of the axis
plt.xlim(-1, 30)
plt.ylim(-1, 30)

# 1 for 1 line

fig = plt.figure(1)
plt.plot(x, y, color = 'black')
fig.savefig('predicted_Observed_Validation_78.png',dpi=600)
plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde

# data to plot
x = predicted
y = ydata

# Calculate the point density
xy = np.vstack([x,y])
z = gaussian_kde(xy)(xy)

# Sort the points by density, so that the densest points are plotted last
idx = z.argsort()
x, y, z = x[idx], y[idx], z[idx]


fig, ax = plt.subplots()
ax.scatter(x, y, c=z, s=0.5, edgecolor='')

# data for the 1 for 1 line
a = [-1,30]
b = [-1,30]

#sets the limits of the axis
plt.xlim(-1,30)
plt.ylim(-1,30)
plt.ylabel('Observed mean CHM')
plt.xlabel('Predicted mean CHM')
# 1 for 1 line
ax.plot(a, b, color = 'black')

plt.show()

In [ ]:
with open('rfr_modelName_mKath', 'rb') as f:
        rf = cPickle.load(f)

        predicted = rf.predict(xdata2)

#print 'r2 =' ,  rf.score(predicted, y_2)
#print 'rmse =', np.sqrt(np.mean((y_2 - predicted)**2))
#print 'n =' , len(y_2)

print 'Predicted data r2 =', rf.score(xdata2, ydata)
print 'MSE =', format(np.mean((ydata - rf.predict(xdata2))** 2), '.3f')
print 'RMSE =', format(np.sqrt(np.mean((predicted - ydata) ** 2)), '.3f')
print 'explained_var =',format(explained_variance_score(ydata, predicted),  '.3f') 
print 'bias =' , format(np.mean(ydata) - np.mean(predicted), '.3f')
print 'n =' , len(ydata)


# plot up predicted and observed data 
plt.scatter(predicted, ydata,s=0.002, c='b', marker='o')

# data for the 1 for 1 line
x = [-1,30]
y = [-1,30]

#sets the limits of the axis
plt.xlim(-1, 30)
plt.ylim(-1, 30)

# 1 for 1 line

fig = plt.figure(1)
plt.plot(x, y, color = 'black')
fig.savefig('predicted_Observed_Validation_l57.png',dpi=600)
plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde

# data to plot
x = predicted
y = ydata

# Calculate the point density
xy = np.vstack([x,y])
z = gaussian_kde(xy)(xy)

# Sort the points by density, so that the densest points are plotted last
idx = z.argsort()
x, y, z = x[idx], y[idx], z[idx]


fig, ax = plt.subplots()
ax.scatter(x, y, c=z, s=0.5, edgecolor='')

# data for the 1 for 1 line
a = [-1,30]
b = [-1,30]

#sets the limits of the axis
plt.xlim(-1,30)
plt.ylim(-1,30)
plt.ylabel('Observed mean CHM')
plt.xlabel('Predicted mean CHM')
# 1 for 1 line
ax.plot(a, b, color = 'black')

plt.show()

In [ ]:
with open('rfr_modelNamel57', 'rb') as f:
        rf = cPickle.load(f)

        predicted = rf.predict(xdata2)

#print 'r2 =' ,  rf.score(predicted, y_2)
#print 'rmse =', np.sqrt(np.mean((y_2 - predicted)**2))
#print 'n =' , len(y_2)

print 'Predicted data r2 =', rf.score(xdata2, ydata)
print 'MSE =', format(np.mean((ydata - rf.predict(xdata2))** 2), '.3f')
print 'RMSE =', format(np.sqrt(np.mean((predicted - ydata) ** 2)), '.3f')
print 'explained_var =',format(explained_variance_score(ydata, predicted),  '.3f') 
print 'bias =' , format(np.mean(ydata) - np.mean(predicted), '.3f')
print 'n =' , len(ydata)


# plot up predicted and observed data 
plt.scatter(predicted, ydata,s=0.002, c='b', marker='o')

# data for the 1 for 1 line
x = [-1,30]
y = [-1,30]

#sets the limits of the axis
plt.xlim(-1, 30)
plt.ylim(-1, 30)

# 1 for 1 line

fig = plt.figure(1)
plt.plot(x, y, color = 'black')
fig.savefig('predicted_Observed_Validation.png',dpi=600)
plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde

# data to plot
x = predicted
y = ydata

# Calculate the point density
xy = np.vstack([x,y])
z = gaussian_kde(xy)(xy)

# Sort the points by density, so that the densest points are plotted last
idx = z.argsort()
x, y, z = x[idx], y[idx], z[idx]


fig, ax = plt.subplots()
ax.scatter(x, y, c=z, s=0.5, edgecolor='')

# data for the 1 for 1 line
a = [-1,30]
b = [-1,30]

#sets the limits of the axis
plt.xlim(-1,30)
plt.ylim(-1,30)
plt.ylabel('Observed mean CHM')
plt.xlabel('Predicted mean CHM')
# 1 for 1 line
ax.plot(a, b, color = 'black')

plt.show()

In [ ]:
with open('rfr_modelNamel57', 'rb') as f:
        rf = cPickle.load(f)

        predicted = rf.predict(xdata2)

#print 'r2 =' ,  rf.score(predicted, y_2)
#print 'rmse =', np.sqrt(np.mean((y_2 - predicted)**2))
#print 'n =' , len(y_2)

print 'Predicted data r2 =', rf.score(xdata2, ydata)
print 'MSE =', format(np.mean((ydata - rf.predict(xdata2))** 2), '.3f')
print 'RMSE =', format(np.sqrt(np.mean((predicted - ydata) ** 2)), '.3f')
print 'explained_var =',format(explained_variance_score(ydata, predicted),  '.3f') 
print 'bias =' , format(np.mean(ydata) - np.mean(predicted), '.3f')
print 'n =' , len(ydata)


# plot up predicted and observed data 
plt.scatter(predicted, ydata,s=0.002, c='b', marker='o')

# data for the 1 for 1 line
x = [-1,30]
y = [-1,30]

#sets the limits of the axis
plt.xlim(-1, 30)
plt.ylim(-1, 30)

# 1 for 1 line

fig = plt.figure(1)
plt.plot(x, y, color = 'black')
fig.savefig('predicted_Observed_Validationgtr4m.png',dpi=600)
plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import gaussian_kde

# data to plot
x = predicted
y = ydata

# Calculate the point density
xy = np.vstack([x,y])
z = gaussian_kde(xy)(xy)

# Sort the points by density, so that the densest points are plotted last
idx = z.argsort()
x, y, z = x[idx], y[idx], z[idx]


fig, ax = plt.subplots()
ax.scatter(x, y, c=z, s=0.5, edgecolor='')

# data for the 1 for 1 line
a = [-1,30]
b = [-1,30]

#sets the limits of the axis
plt.xlim(-1,30)
plt.ylim(-1,30)
plt.ylabel('Observed mean CHM')
plt.xlabel('Predicted mean CHM')
# 1 for 1 line
ax.plot(a, b, color = 'black')

plt.show()

In [ ]:
with open('rfr_modelNamel78', 'rb') as f:
        rf = cPickle.load(f)

        predicted = rf.predict(xdata2)

#print 'r2 =' ,  rf.score(predicted, y_2)
#print 'rmse =', np.sqrt(np.mean((y_2 - predicted)**2))
#print 'n =' , len(y_2)

print 'Predicted data r2 =', rf.score(xdata2, ydata)
print 'MSE =', format(np.mean((ydata - rf.predict(xdata2))** 2), '.3f')
print 'RMSE =', format(np.sqrt(np.mean((predicted - ydata) ** 2)), '.3f')
print 'explained_var =',format(explained_variance_score(ydata, predicted),  '.3f') 
print 'bias =' , format(np.mean(ydata) - np.mean(predicted), '.3f')
print 'n =' , len(ydata)


# plot up predicted and observed data 
plt.scatter(predicted, ydata,s=0.002, c='b', marker='o')

# data for the 1 for 1 line
x = [-1,30]
y = [-1,30]

#sets the limits of the axis
plt.xlim(-1, 30)
plt.ylim(-1, 30)

# 1 for 1 line

fig = plt.figure(1)
plt.plot(x, y, color = 'black')
fig.savefig('predicted_Observed_Validation.png',dpi=600)
plt.show()